In [63]:
import altair as alt
import geopandas as gpd
import json
import pandas as pd

geojson_loc = r"C:\Users\mille\PycharmProjects\VisualizingPower\venv\Include\Philly\PhiladelphiaWardDivisions201201.geojson"
vote_excel_loc = r"C:\Users\mille\PycharmProjects\VisualizingPower\venv\Include\Philly\Committeeperson_Winners_-_Democratic_Public_List.xlsx"

def open_geojson():
    with open(geojson_loc) as json_data:
        d = json.load(json_data)
    return d

philly_json = open_geojson()
gdfjson = gpd.GeoDataFrame.from_features((philly_json))
gdfjson['NAME2_'] = gdfjson['NAME2_'].apply(lambda x: str(x))

df = pd.read_excel(vote_excel_loc, index_col=None)
df['trimmed_precinct'] = df['PRECINCT'].apply(lambda x : str(x).replace('-', ''))

gdf = gdfjson.merge(df, left_on='NAME2_', right_on='trimmed_precinct', how='left')
chloro_json = json.loads(gdf.to_json())
chloro_data = alt.Data(values=chloro_json['features'])

In [68]:
def gen_map(geodata, color_column, title, tooltip, color_scheme='bluegreen'):
    
    # Add Base Layer
    base = alt.Chart(geodata, title = title).mark_geoshape(
        fill='lightgray',
        stroke='black',
        strokeWidth=1
    ).encode(
    ).properties(
        width=800,
        height=800
    )
    
    # Add Choropleth Layer
    chloro = alt.Chart(geodata).mark_geoshape(
        #fill='lightgray',
        stroke='black'
    ).encode(
        alt.Color(color_column, 
              type='quantitative', 
              scale=alt.Scale(scheme=color_scheme),
              title = "Turn Out"),
        tooltip=tooltip
    )
    return base + chloro

In [69]:
gen_map(geodata=chloro_data, color_column='properties.TOTAL:O', title="Philly", tooltip='properties.PRECINCT:N')

alt.LayerChart(...)

In [62]:
gdf[['PRECINCT', 'TOTAL']]

PRECINCT  TOTAL
0       66-23   43.0
1       66-23   42.0
2       58-30   32.0
3       58-30   21.0
4       58-14   24.0
...       ...    ...
3067    05-25   45.0
3068    05-27  151.0
3069    05-27    3.0
3070    24-18    1.0
3071    24-19    1.0

[3072 rows x 2 columns]